#The code is responsible for creating tables in a MySQL database. To perform this task, it establishes a connection to the MySQL server using a specific username and password provided by the user. This connection allows the code to execute SQL queries to create the necessary tables in the database. 

In [1]:
import mysql.connector
import json
from datetime import datetime

In [10]:
# Connect to a MySQL database
conn = mysql.connector.connect(
    host='localhost',
    user='root',
    password='Kum@r123',
    database="Twitter26"
)

# Create a cursor object
cursor = conn.cursor()


In [9]:
#cursor = conn.cursor()
#cursor.execute("CREATE DATABASE Twitter03")

In [11]:

# Create a table for users
cursor.execute('''CREATE TABLE user
             (user_id BIGINT NOT NULL PRIMARY KEY,
             user_id_str VARCHAR(255),
             name VARCHAR(255),
             screen_name VARCHAR(255),
             location VARCHAR(255),
             description TEXT,
             protected VARCHAR(10),
             verified VARCHAR(10),
             followers_count INTEGER,
             friends_count INTEGER,
             favourites_count INTEGER,
             statuses_count INTEGER,
             created_at VARCHAR(255),
             media_url VARCHAR(255))''')

# a table for tweets
cursor.execute('''CREATE TABLE tweet
             (tweet_id BIGINT NOT NULL PRIMARY KEY,
             tweet_id_str VARCHAR(255),
             user_id BIGINT NOT NULL,
             in_reply_to_status_id INTEGER,
             in_reply_to_status_id_str VARCHAR(255),
             in_reply_to_user_id INTEGER,
             in_reply_to_user_id_str VARCHAR(255),
             in_reply_to_screen_name VARCHAR(255),
             reply_count INTEGER,
             retweet_count INTEGER,
             favorite_count INTEGER,
             retweeted VARCHAR(10),
             filter_level VARCHAR(10),
             possible_sensitivity VARCHAR(10),
             FOREIGN KEY (user_id) REFERENCES user(user_id))''')
#a table for retweets
cursor.execute('''CREATE TABLE retweet
             (retweet_id BIGINT NOT NULL PRIMARY KEY,
             retweet_id_str VARCHAR(255),
             user_id BIGINT NOT NULL,
             tweet_id BIGINT NOT NULL,
             in_reply_to_status_id BIGINT,
             in_reply_to_status_id_str VARCHAR(255),
             in_reply_to_user_id BIGINT,
             in_reply_to_user_id_str VARCHAR(255),
             in_reply_to_screen_name VARCHAR(255),
             reply_count BIGINT,
             retweet_count BIGINT,
             favorite_count BIGINT,
             retweeted TINYINT(1) NOT NULL DEFAULT 0,
             filter_level VARCHAR(10),
             possible_sensitivity VARCHAR(10),
             FOREIGN KEY (user_id) REFERENCES user(user_id),
             FOREIGN KEY (tweet_id) REFERENCES tweet(tweet_id))''')
#a tablr for hastags
cursor.execute('''CREATE TABLE hashtag 
             (hashtag_id BIGINT NOT NULL AUTO_INCREMENT PRIMARY KEY,
             name VARCHAR(255))''')
#a table for composite key
# PRIMARY KEY (tweet_id, hashtag_id),
cursor.execute('''CREATE TABLE tweet_hashtag
             (tweet_id BIGINT NOT NULL,
              hashtag_id BIGINT NOT NULL,
              FOREIGN KEY (tweet_id) REFERENCES tweet(tweet_id),
              FOREIGN KEY (hashtag_id) REFERENCES hashtag(hashtag_id))''');

In [13]:
with open('corona.json', 'r') as f:
  
    for line in f:
       
        try:
            
            data = json.loads(line)
            
            #Inserting Tweet User data
            user_id = data['user']['id'] if 'id' in data['user'] else None
            user_id_str = data['user']['id_str'] if 'id_str' in data['user'] else None
            name = data['user']['name'] if 'name' in data['user'] else None
            screen_name = data['user']['screen_name'] if 'screen_name' in data['user'] else None
            location = data['user']['location'] if 'location' in data['user'] else None
            description = data['user']['description'] if 'description' in data['user'] else None
            protected = data['user']['protected'] if 'protected' in data['user'] else None
            verified = data['user']['verified'] if 'verified' in data['user'] else None
            followers_count = data['user']['followers_count'] if 'followers_count' in data['user'] else None
            friends_count = data['user']['friends_count'] if 'friends_count' in data['user'] else None
            favourites_count = data['user']['favourites_count'] if 'favourites_count' in data['user'] else None
            statuses_count = data['user']['statuses_count'] if 'statuses_count' in data['user'] else None
            created_at = data['user']['created_at'] if 'created_at' in data['user'] else None

            # check if user has a profile image
            if 'profile_image_url_https' in data['user']:
                media_url =data['user']['profile_image_url_https']
            else:
                media_url = ""
            sql = """INSERT INTO user (user_id, user_id_str, name, screen_name, location, description, protected, verified, followers_count, friends_count, favourites_count, statuses_count, created_at, media_url) 
                     VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)"""
            values = (user_id, user_id_str, name, screen_name, location, description, protected, verified, followers_count, friends_count, favourites_count, statuses_count, created_at, media_url)
            cursor.execute(sql, values)
            print('user')
            
            # Inserting data into tweets table
            tweet_query = '''INSERT INTO tweet (tweet_id, tweet_id_str, user_id, in_reply_to_status_id, 
                          in_reply_to_status_id_str, in_reply_to_user_id, in_reply_to_user_id_str, in_reply_to_screen_name,
                          reply_count, retweet_count, favorite_count, retweeted) 
                          VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)'''
            
            tweet_values = (data['id'], data['id_str'], data['user']['id'], data['in_reply_to_status_id'], 
                            data['in_reply_to_status_id_str'], data['in_reply_to_user_id'], 
                            data['in_reply_to_user_id_str'], data['in_reply_to_screen_name'], 
                            data['reply_count'], data['retweet_count'], data['favorite_count'], data['retweeted'])
            
            cursor.execute(tweet_query, tweet_values)
            print(data['id'],'tweet')
            
            #Inserting Retweet User Data
            if 'retweeted_status' in data:
                
                retweet = data['retweeted_status']
                # extract the necessary fields from the user_data object
                user_data = retweet['user']
                user_id = user_data['id']
                user_id_str = user_data['id_str']
                name = user_data['name']
                screen_name = user_data['screen_name']
                location = user_data['location']
                description = user_data['description']
                protected = user_data['protected']
                verified = user_data['verified']
                followers_count = user_data['followers_count']
                friends_count = user_data['friends_count']
                favourites_count = user_data['favourites_count']
                statuses_count = user_data['statuses_count']
                created_at_str = user_data['created_at']
                created_at = ''
                profile_background_image_url = ''

                # Inserting the data into the user table
                user_query = """
                    INSERT INTO user 
                    (user_id, user_id_str, name, screen_name, location, description, protected, verified, 
                    followers_count, friends_count, favourites_count, statuses_count, created_at, 
                    media_url) 
                    VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
                """
                
                user_values = (user_id, user_id_str, name, screen_name, location, description, protected, 
                               verified, followers_count, friends_count, favourites_count, 
                               statuses_count,created_at,profile_background_image_url)
                
                cursor.execute(user_query, user_values)
                print('retweetuser')
               

                #Inserting retweet data
                # Check if all the required fields are present in the retweeted tweet
                if 'id' in retweet and 'id_str' in retweet and 'user' in retweet \
                    and 'id' in retweet['user'] and 'id' in tweet and 'reply_count' in retweet \
                    and 'retweet_count' in retweet and 'favorite_count' in retweet \
                    and 'retweeted' in tweet:

                    # Extract the required fields from the retweeted tweet
                    retweet_id = retweet['id'] if 'id' in retweet else None
                    retweet_id_str = retweet['id_str'] if 'id_str' in retweet else None
                    user_id = retweet['user']['id'] if 'id' in retweet['user'] else None
                    tweet_id = tweet['id'] if 'id' in tweet else None
                    in_reply_to_status_id = retweet['in_reply_to_status_id'] if 'in_reply_to_status_id' in retweet else None
                    in_reply_to_status_id_str = retweet['in_reply_to_status_id_str'] if 'in_reply_to_status_id_str' in retweet else None
                    in_reply_to_user_id = retweet['in_reply_to_user_id'] if 'in_reply_to_user_id' in retweet else None
                    in_reply_to_user_id_str = retweet['in_reply_to_user_id_str'] if 'in_reply_to_user_id_str' in retweet else None
                    in_reply_to_screen_name = retweet['in_reply_to_screen_name'] if 'in_reply_to_screen_name' in retweet else None
                    reply_count = retweet['reply_count'] if 'reply_count' in retweet else None
                    retweet_count = retweet['retweet_count'] if 'retweet_count' in retweet else None
                    favorite_count = retweet['favorite_count'] if 'favorite_count' in retweet else None
                    retweeted = 1 if retweet['retweeted'] else 0
                    filter_level = ''
                    possible_sensitivity = ''
                    sql = "INSERT INTO retweet (retweet_id, retweet_id_str, user_id, tweet_id, " \
                              "in_reply_to_status_id, in_reply_to_status_id_str, in_reply_to_user_id, " \
                              "in_reply_to_user_id_str, in_reply_to_screen_name, reply_count, retweet_count, " \
                              "favorite_count, retweeted,filter_level,possible_sensitivity) " \
                              "VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)"
                    val = (retweet_id, retweet_id_str, user_id, tweet_id, in_reply_to_status_id,
                               in_reply_to_status_id_str, in_reply_to_user_id, in_reply_to_user_id_str,
                               in_reply_to_screen_name, reply_count, retweet_count, favorite_count,
                               retweeted,filter_level,possible_sensitivity)
                    cursor.execute(sql, val)
                    print('retweet')
            

            
             #Inserting data into hastag table
            if 'entities' in data and 'hashtags' in data['entities']:
                for hashtag in data['entities']['hashtags']:
                    if isinstance(hashtag['text'], str):
                        hashtag_str = hashtag['text']
                    elif isinstance(hashtag['text'], int):
                        hashtag_str = str(hashtag['text'])
                # Insert the hashtag data if it doesn't exist
                    query = "INSERT IGNORE INTO hashtag (name) VALUES (%s)"
                    hasht = hashtag['text']
                    values = (hashtag_str,)
                    print(hashtag['text'],'hash')
                    cursor.execute(query, values)
                    print('as')

                    # Get the hashtag_id from the hashtag table
                    query = "SELECT hashtag_id FROM hashtag WHERE name = %s limit 1"
                    values = (hashtag_str,)
                   
                    cursor.execute(query, values)
                    print('qw')
                    result = cursor.fetchone()
                   
                    if result:
                        hashtag_id = result[0]
                        # Insert the tweet_hashtag data
                        query = "INSERT INTO tweet_hashtag (tweet_id, hashtag_id) VALUES (%s, %s)"
                        values = (data['id'], hashtag_id)
                        cursor.execute(query, values)
                        print('we')
                    conn.commit()
      





             
        except:
            continue 
            
        

        
            
            
            
            



user
1254022770679320576 tweet
user
1254022770746372096 tweet
sport hash
as
qw
we
corona hash
as
qw
we
user
1254022772558368768 tweet
retweetuser
user
1254022772575043586 tweet
user
1254022772877131777 tweet
user
1254022773149589510 tweet
retweetuser
user
1254022773858545665 tweet
retweetuser
user
1254022774521081856 tweet
retweetuser
user
user
1254022776094105602 tweet
user
1254022776232394752 tweet
retweetuser
user
user
1254022776752615430 tweet
user
1254022777268568064 tweet
retweetuser
user
1254022778363265024 tweet
retweetuser
user
1254022778371571712 tweet
user
1254022779608891393 tweet
user
1254022780695252993 tweet
user
1254022780980527105 tweet
retweetuser
user
1254022781093601280 tweet
retweetuser
user
1254022781722923009 tweet
retweetuser
user
1254022781873856512 tweet
retweetuser
user
1254022782188261376 tweet
retweetuser
user
1254022782561718272 tweet
retweetuser
user
user
1254022783480332288 tweet
user
user
1254022784323252225 tweet
retweetuser
user
1254022784122003457 tw

user
1254022889810034688 tweet
user
1254022889948557314 tweet
retweetuser
user
1254022889013235713 tweet
user
1254022890216816641 tweet
user
1254022890770452480 tweet
retweetuser
user
1254022892200833026 tweet
user
1254022892993552386 tweet
user
1254022893148737536 tweet
retweetuser
user
1254022893635162112 tweet
retweetuser
user
1254022893756772352 tweet
retweetuser
user
1254022893962432513 tweet
user
1254022894243450882 tweet
retweetuser
user
1254022894155431936 tweet
RIVM hash
as
qw
we
Brabant hash
as
qw
we
user
user
1254022894528708608 tweet
user
1254022895061393408 tweet
user
1254022895094779905 tweet
retweetuser
user
1254022895522717696 tweet
user
1254022894730051585 tweet
user
1254022896780898304 tweet
user
1254022896613122048 tweet
retweetuser
user
1254022896923672576 tweet
user
1254022897120579586 tweet
user
1254022897347162114 tweet
user
1254022897733156866 tweet
user
1254022898655719425 tweet
user
1254022898752290821 tweet
user
1254022899146637313 tweet
retweetuser
user
user

retweetuser
user
1254022982327992320 tweet
retweetuser
user
1254022982869168129 tweet
retweetuser
user
1254022983481524225 tweet
retweetuser
user
1254022983535992832 tweet
user
1254022984102219776 tweet
user
1254022984735621120 tweet
user
1254022985989701633 tweet
user
1254022986086199296 tweet
retweetuser
user
1254022985872261121 tweet
user
1254022986425946115 tweet
user
1254022986568474624 tweet
retweetuser
user
1254022986799038465 tweet
user
1254022986849550336 tweet
user
1254022986950160386 tweet
user
1254022987331727363 tweet
user
1254022987210252289 tweet
user
1254022987881349121 tweet
retweetuser
user
1254022988413808640 tweet
retweetuser
user
1254022988586004480 tweet
retweetuser
user
1254022989353349121 tweet
retweetuser
user
1254022989416411136 tweet
user
1254022989752000512 tweet
user
1254022990444007425 tweet
user
user
user
1254022993224884225 tweet
user
1254022993229090816 tweet
retweetuser
user
user
1254022994135040001 tweet
retweetuser
user
1254022994625617923 tweet
retw

user
1254023084518060034 tweet
user
user
1254023104604471298 tweet
user
1254023105137250304 tweet
user
1254023105787330560 tweet
retweetuser
user
1254023106269794305 tweet
user
1254023106705993729 tweet
retweetuser
user
1254023107322556421 tweet
retweetuser
user
user
1254023108132048896 tweet
user
1254023101656023040 tweet
user
1254023108731768833 tweet
retweetuser
user
1254023108828291072 tweet
retweetuser
user
user
1254023109608443904 tweet
retweetuser
user
user
1254023110212411398 tweet
retweetuser
user
1254023110547947520 tweet
retweetuser
user
user
user
1254023111613259776 tweet
user
user
user
1254023112661831680 tweet
retweetuser
user
1254023112276008960 tweet
user
1254023112955494400 tweet
user
1254023113236504576 tweet
retweetuser
user
1254023113685139464 tweet
user
1254023113555111937 tweet
user
1254023114025054211 tweet
user
1254023114586877952 tweet
user
1254023114511405061 tweet
user
1254023115241222145 tweet
retweetuser
user
1254023115559952390 tweet
user
12540231160760688

1254023212284833793 tweet
user
1254023212331077632 tweet
retweetuser
user
user
1254023212784144384 tweet
user
user
1254023214151458818 tweet
user
1254023214222774277 tweet
user
1254023214503735297 tweet
GeschichteFürZuhause hash
as
qw
we
user
1254023215288127493 tweet
user
user
1254023215279755264 tweet
retweetuser
user
user
1254023214927208449 tweet
user
1254023216940670976 tweet
retweetuser
user
1254023218257702912 tweet
user
1254023218383314945 tweet
retweetuser
user
1254023219201204224 tweet
retweetuser
user
1254023219826188288 tweet
user
1254023219872325637 tweet
user
1254023220438749184 tweet
user
1254023220736471041 tweet
retweetuser
user
1254023221361467395 tweet
retweetuser
user
1254023222716178432 tweet
user
1254023222812647425 tweet
helicoptermoney hash
as
qw
we
user
1254023224523993088 tweet
retweetuser
user
user
1254023225425694720 tweet
retweetuser
user
1254023225366818822 tweet
user
1254023225509543938 tweet
user
1254023225501036545 tweet
user
1254023226046349314 tweet
u

...

user
1254059104739323904 tweet
user
user
1254059105402195968 tweet
user
1254059106564034560 tweet
user
1254059106899558400 tweet
user
1254059108434620419 tweet
user
1254059108547702785 tweet
user
1254059109583859716 tweet
user
1254059109613174785 tweet
user
1254059110145941512 tweet
user
1254059110187794432 tweet
user
user
1254059110942806018 tweet
user
1254059112008212481 tweet
user
1254059113018994690 tweet
user
1254059113371271171 tweet
user
1254059113895669763 tweet
user
user
1254059115443347457 tweet
user
1254059116022161408 tweet
user
1254059116022161409 tweet
user
1254059116378689537 tweet
user
1254059117171228677 tweet
user
1254059117297139721 tweet
user
1254059118136090625 tweet
user
user
1254059119000027137 tweet
user
1254059120203829249 tweet
user
1254059120270823424 tweet
user
user
1254059121097261058 tweet
user
1254059121994678273 tweet
user
1254059121952690177 tweet
user
user
1254059122087133189 tweet
user
1254059124771319808 tweet
user
1254059125010575360 tweet
user
1254

1254059250021736449 tweet
user
1254059250546073601 tweet
user
user
1254059250726440961 tweet
user
1254059251044978688 tweet
user
1254059251984629761 tweet
user
1254059254551625728 tweet
user
1254059255273009157 tweet
user
1254059255411478529 tweet
user
1254059255868674049 tweet
retweetuser
user
1254059256141283328 tweet
Corona hash
as
qw
we
user
1254059257357651971 tweet
user
1254059258745937920 tweet
user
1254059259710636032 tweet
user
1254059259844853760 tweet
retweetuser
user
user
1254059261216374788 tweet
user
1254059261723893760 tweet
COVID19 hash
as
qw
we
user
1254059261564293120 tweet
user
1254059262072012800 tweet
user
1254059262289928192 tweet
user
1254059262759915520 tweet
user
1254059262998970370 tweet
user
1254059263682584576 tweet
user
1254059263372128261 tweet
user
1254059264425017344 tweet
user
1254059264550645760 tweet
user
1254059264538226689 tweet
user
user
1254059265670742016 tweet
user
1254059266123628544 tweet
user
1254059266748682241 tweet
user
1254059267138740225

user
1254059380082950144 tweet
user
1254059380414255106 tweet
user
user
1254059380473020416 tweet
user
1254059380430995456 tweet
user
1254059380871516161 tweet
user
user
1254059381366259713 tweet
user
1254059381173268480 tweet
user
1254059381311762433 tweet
retweetuser
user
1254059381559353346 tweet
retweetuser
user
1254059381534134274 tweet
user
user
1254059382385651712 tweet
user
1254059383933280256 tweet
user
1254059384373739521 tweet
user
1254059384759627776 tweet
2020WasFunUntil hash
as
qw
we
user
1254059385468456961 tweet
user
1254059385866850305 tweet
user
1254059386605092865 tweet
user
1254059383924932609 tweet
user
1254059387645161473 tweet
user
1254059387678834688 tweet
user
1254059388446392322 tweet
user
1254059388387680256 tweet
user
1254059389025214466 tweet
user
1254059389406846979 tweet
user
1254059389608235008 tweet
user
user
1254059391004717056 tweet
user
1254059393135583233 tweet
user
1254059393441816576 tweet
user
user
1254059395228499968 tweet
user
user
125405939660

1254059507895984134 tweet
user
1254059507946344450 tweet
books hash
as
qw
we
readingadvice hash
as
qw
we
brandonsanderson hash
as
qw
we
user
1254059507925364736 tweet
retweetuser
user
1254059508311171072 tweet
user
1254059508717977600 tweet
user
1254059509028278272 tweet
user
1254059509556875264 tweet
user
1254059509514825729 tweet
user
1254059509535784961 tweet
user
1254059509686951936 tweet
user
1254059509716320256 tweet
user
1254059509779255300 tweet
user
1254059510190297088 tweet
user
1254059510517452800 tweet
user
1254059511314288640 tweet
user
1254059511867936768 tweet
user
1254059511888769025 tweet
user
user
1254059513273081856 tweet
user
1254059514090991625 tweet
user
1254059514275520512 tweet
retweetuser
user
1254059514631839746 tweet
user
1254059514845954049 tweet
user
user
user
user
1254059517261877249 tweet
user
1254059517215682560 tweet
user
1254059517895204867 tweet
user
user
1254059519275159555 tweet
RescUE hash
as
qw
we
Corona hash
as
qw
we
user
1254059519728062465 twee

as
qw
we
Berlin hash
as
qw
we
user
1254059632907059202 tweet
user
1254059633095987202 tweet
user
1254059633829908480 tweet
user
1254059634073038848 tweet
user
1254059633901215750 tweet
user
1254059634375131146 tweet
user
1254059634706579456 tweet
user
user
1254059634765238272 tweet
user
1254059635142688776 tweet
user
1254059635255934983 tweet
user
1254059637504172033 tweet
user
1254059638032490497 tweet
user
user
1254059638070423556 tweet
user
1254059638279962630 tweet
user
user
1254059638284341249 tweet
Corona hash
as
qw
we
Soloselbststaendige hash
as
qw
we
user
1254059639362203648 tweet
user
1254059640150687745 tweet
user
1254059640486334470 tweet
user
user
1254059641258065920 tweet
user
1254059641937342470 tweet
user
user
1254059642138669056 tweet
user
1254059642373668864 tweet
user
1254059643044720641 tweet
retweetuser
user
1254059644420419584 tweet
user
1254059644546318337 tweet
user
user
1254059644810440705 tweet
user
1254059644726784005 tweet
user
1254059645083291649 tweet
user
